In [1]:
# Import required libraries for data manipulation and analysis
import pandas as pd
from pandas import read_csv
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import time

In [2]:
#Import required sklearn functions
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import SelectFromModel
from sklearn.feature_selection import VarianceThreshold

In [3]:
#Import sklearn classifiers
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.svm import SVC
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.gaussian_process.kernels import RBF
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB

In [4]:
#Import library to oversample 
from imblearn.over_sampling import RandomOverSampler

In [5]:
#Import RDKit and Mordred libraries
from rdkit import Chem
from rdkit.Chem import Draw
from mordred import Calculator, descriptors

In [6]:
#Allows figures to be visualized in jupyter notebook
%matplotlib inline

In [7]:
# Sets Pandas Display to Monitor Code
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 15)

In [8]:
# Create Mordred Calculator
calc = Calculator(descriptors, ignore_3D=True)

In [9]:
# Read Training/Test data input File
data = pd.read_csv('BorylationTrainingTest.csv')

In [10]:
# Assigns Reactants Mordred Info
reactants = data['Substrate']

reactants_mol_list = []
for inChi_reactants in reactants:
  reactants_mol = Chem.MolFromInchi(inChi_reactants)
  reactants_mol_list.append(reactants_mol)

reactants_img = Draw.MolsToGridImage(reactants_mol_list, molsPerRow=4)

/home/sweav003/envs/CHB/lib/python3.7/site-packages/rdkit/Chem/Draw/IPythonConsole.py:192: UserWarning: Truncating the list of molecules to be displayed to 50. Change the maxMols value to display more.
  % (maxMols))


In [11]:
# Puts reactants into Pandas Type
reactant_data = []
reactant_data = calc.pandas(reactants_mol_list)
reactant_data.info()

100%|██████████| 680/680 [01:02<00:00, 10.82it/s]


<class 'mordred._base.pandas_module.MordredDataFrame'>
RangeIndex: 680 entries, 0 to 679
Columns: 1613 entries, ABC to mZagreb2
dtypes: bool(2), float64(900), int64(324), object(387)
memory usage: 8.4+ MB


In [12]:
#Joins Mordred parameters with experimental, atomic charges, and JChem for Excel parameters
add_reactants = pd.concat((data, reactant_data), axis=1)

In [13]:
#Force any non-numeric entries as NaN and replace them with 0
final_data = add_reactants.apply(pd.to_numeric, errors='coerce')
final_data.fillna(0, inplace=True)
final_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 680 entries, 0 to 679
Columns: 1669 entries, Substrate to mZagreb2
dtypes: bool(2), float64(1316), int64(351)
memory usage: 8.6 MB


In [14]:
# Seperate dataset as response variable (Product Ratio) and feature variables
#Note: Product Ratio is described as "0" for non-borylating sites and "1" for borylating sites
X = final_data.drop('Product_Ratio' , axis = 1)
y = final_data['Product_Ratio']

In [15]:
#Remove any features that have zero variance, i.e. remain the same number for every entry
sel = VarianceThreshold()
_ = sel.fit(X)
mask = sel.get_support()
X = X.loc[:,mask]

In [16]:
#Remove any features that are greater than 95% correlated
corr_matrix = X.corr()
upper_tri = corr_matrix.where(np.triu(np.ones(corr_matrix.shape),k=1).astype(np.bool))

to_drop = [column for column in upper_tri.columns if any(upper_tri[column] > 0.95)]

Final = X.drop(to_drop, axis = 1)
corr_matrix=Final.corr()

plt.figure(figsize = (10, 10),dpi=1000)
sns.heatmap(
    corr_matrix, 
    annot =False,
    vmin=-1, vmax=1, center=0,
    cmap=sns.diverging_palette(20, 220, n=200),
    square=True
   )

plt.show()

In [17]:
# Specifys Random Forest and the Number of Trees, SelectFromModel will
# select features which are most important
feature_names = [f"feature {i}" for i in range(Final.shape[1])]
forest = RandomForestClassifier(random_state=42)
forest.fit(Final, y)

start_time = time.time()
importances = forest.feature_importances_
std = np.std([tree.feature_importances_ for tree in forest.estimators_], axis=0)
elapsed_time = time.time() - start_time

threshold = np.sort(importances)[-100] 
sel = SelectFromModel(RandomForestClassifier(n_estimators = 800, max_depth=30),threshold=threshold)
sel.fit(Final, y)

# Select the final features set 
sel.get_support()
selected_feat= Final.columns[(sel.get_support())]

# Prints the names of the final selected features
print(selected_feat)

Index(['Hirshfeld Heavy Atom Charge', 'CM5 Charge', 'Hirshfeld Carbon Charge',
       'Hirshfeld Hydrogen Charge', 'ESP Heavy Atom Charge',
       'ESP Carbon Charge', 'ESP Hydrogen Charge', 'NPA Carbon Charge',
       'NPA Hydrogen Charge', 'MBS Carbon Charge', 'MBS Hydrogen Charge',
       'Mulliken Heavy Charge', 'Mulliken Carbon Charge',
       'Mulliken Hydrogen Charge', 'Steric Effect Index',
       'Atomic_Polarizability', 'Distance Degree', 'Dreiding Energy',
       'Eccentricity', 'Max Projection Area', 'Max Projection Radius', 'MaxZ',
       'Sigma Electronegativity', 'SpMax_A', 'VR1_A', 'ATS0p', 'AATS2Z',
       'AATS0v', 'AATS3v', 'AATS4v', 'AATS3p', 'AATS4i', 'AATSC5Z', 'AATSC2v',
       'GATS2c', 'GATS3c', 'GATS5i', 'BCUTd-1h', 'BCUTZ-1l', 'Xch-7dv',
       'AETA_eta_L', 'SIC0', 'AMID_h', 'TSRW10'],
      dtype='object')


In [18]:
#Create final dataframe for training and testing
final = X[selected_feat]

In [19]:
#Visualize the spearman correlation of the final features of dataset
corr_matrix = final.corr(method="spearman")

plt.figure(figsize = (10, 10),dpi=1000)
ax = sns.heatmap(
    corr_matrix, 
    annot =False,
    vmin=-1, vmax=1, center=0,
    cmap="YlGnBu",
    square=True,
    cbar_kws={'shrink': 0.82},
    annot_kws={"size": 5}  
   )

plt.show()

In [20]:
#This cell details the machine learning algorithms tested during initial model testing

#Set up training data for learning with final reduced features 
X_train, X_test, y_train, y_test = train_test_split(final, y, test_size=0.20, random_state=31)

#Apply over-sampling to dataset
ros = RandomOverSampler(random_state=10)
X_resampled, y_resampled = ros.fit_resample(X_train, y_train)

#MLP CLassifier
MLP = MLPClassifier(alpha=1, max_iter=1000)
MLP.fit(X_resampled,y_resampled)
pred_MLP = MLP.predict(X_test)
print("MLP Classifier Results")
print(classification_report(y_test, pred_MLP))
print("  ")

#SVM1 CLassifier
SVM1 = SVC(kernel="linear", C=0.025)
SVM1.fit(X_resampled,y_resampled)
pred_SVM1 = SVM1.predict(X_test)
print("SVM1 Classifier Results")
print(classification_report(y_test, pred_SVM1))
print("  ")

#SVM2 CLassifier
SVM2 = SVC(gamma=2, C=1)
SVM2.fit(X_resampled,y_resampled)
pred_SVM2 = SVM2.predict(X_test)
print("SVM2 Classifier Results")
print(classification_report(y_test, pred_SVM2))
print("  ")

#Gaussian Process CLassifier
Gauss = GaussianProcessClassifier(1.0 * RBF(1.0))
Gauss.fit(X_resampled,y_resampled)
pred_Gauss = Gauss.predict(X_test)
print("Gaussian Process Classifier Results")
print(classification_report(y_test, pred_Gauss))
print("  ")

#Decision Tree CLassifier
DT = DecisionTreeClassifier(max_depth=9)
DT.fit(X_resampled,y_resampled)
pred_DT = DT.predict(X_test)
print("Decision Tree Classifier Results")
print(classification_report(y_test, pred_DT))
print("  ")

#Ada Boost CLassifier
ada = AdaBoostClassifier()
ada.fit(X_resampled,y_resampled)
pred_ada = ada.predict(X_test)
print("Ada Boost Classifier Results")
print(classification_report(y_test, pred_ada))
print("  ")

#Naive Bayes CLassifier
NB = GaussianNB()
NB.fit(X_resampled,y_resampled)
pred_NB = NB.predict(X_test)
print("Naive Bayes Classifier Results")
print(classification_report(y_test, pred_NB))
print("  ")

#Random Forest Classifier
rfc = RandomForestClassifier(n_estimators=800,max_depth=9)
rfc.fit(X_resampled,y_resampled)
pred_rfc = rfc.predict(X_test)
print("Random Forest Classifier Results")
print(classification_report(y_test, pred_rfc))

MLP Classifier Results
              precision    recall  f1-score   support

           0       0.80      0.76      0.78       109
           1       0.19      0.22      0.20        27

    accuracy                           0.65       136
   macro avg       0.49      0.49      0.49       136
weighted avg       0.68      0.65      0.66       136

  
SVM1 Classifier Results
              precision    recall  f1-score   support

           0       0.87      0.61      0.72       109
           1       0.29      0.63      0.40        27

    accuracy                           0.62       136
   macro avg       0.58      0.62      0.56       136
weighted avg       0.75      0.62      0.66       136

  
SVM2 Classifier Results
              precision    recall  f1-score   support

           0       0.80      0.94      0.87       109
           1       0.25      0.07      0.11        27

    accuracy                           0.77       136
   macro avg       0.53      0.51      0.49       1

In [21]:
#Loads validation dataset for borlation using the final reduced features 
unknownSubstrates=pd.read_csv('BorylationValidation.csv')

# Convert validation substrates Inchi's to Mordred and combine into Dataframe with atomic charges and JChem paramters
New_Substrate = unknownSubstrates['Substrate']
New_Substrate_mol_list = []
for inChi_New_Substrate in New_Substrate:
  New_Substrate_mol = Chem.MolFromInchi(inChi_New_Substrate)
  New_Substrate_mol_list.append(New_Substrate_mol)

New_Substrate_data = []
New_Substrate_data = calc.pandas(New_Substrate_mol_list)
New_Substrate_data = New_Substrate_data.apply(pd.to_numeric, errors='coerce')
New_Substrate_data.fillna(0, inplace=True)                                                                  
XnewSec = pd.concat((unknownSubstrates, New_Substrate_data), axis=1)
Xnew = XnewSec[selected_feat]


100%|██████████| 79/79 [00:10<00:00,  7.29it/s]


In [22]:
#This cell runs the model ten times, evaluates classification via sklearn metrics and downloads the results to a csv file
totalResults_df = pd.DataFrame(columns = ["True Neg","False Pos","False Neg","True Pos", 'acc', 'precision 0',
                                   'precision 1','recall 0', 'recall 1', 'F1 0', 'F1 1'])
val_tot = pd.DataFrame()
matrix_list = []
for x in range(1, 11):
    #Perform training/test set split
    X_train, X_test, y_train, y_test = train_test_split(final, y, test_size=0.20, random_state=31)

    #Apply over-sampling to dataset
    ros = RandomOverSampler(random_state=10)
    X_resampled, y_resampled = ros.fit_resample(X_train, y_train)

    # Applies random forest classifier to the dataset
    rfc = RandomForestClassifier(n_estimators=800,max_depth=9)
    rfc.fit(X_resampled,y_resampled)
    
    #Make model predictions
    pred_rfc = rfc.predict(X_test)
    
    #Calculate confusion matrix
    cf_matrix = confusion_matrix(y_test, pred_rfc)
    cf_matrix = np.reshape(cf_matrix,(1,4))
    
    #Calculate sklearn classification metrics
    acc = accuracy_score(y_test, pred_rfc)
    prec = precision_score(y_test, pred_rfc, average=None)
    recall = recall_score(y_test, pred_rfc, average=None)
    F1 = f1_score(y_test, pred_rfc, average=None)
    comb = np.concatenate((cf_matrix, acc, prec, recall, F1), axis=None)
    comb = [comb]
    totalResults_df = totalResults_df.append(pd.DataFrame(comb, columns=totalResults_df.columns), ignore_index=True)
    
    #Evaluate the model on validation set
    ynew = rfc.predict(Xnew)
    validation_prediction_df = pd.DataFrame(ynew, columns = [(x)])
    validation_prediction_df.merge(validation_prediction_df, on=x)
    val_pred_T = validation_prediction_df.T
    val_tot = val_tot.append(val_pred_T)     

#Print the classification evaluations for model
print(totalResults_df)    

#Print the validation evaluations for model
unknownSubstrates_prod = unknownSubstrates['Product_Ratio']
total_val_results_transposed = val_tot.T
Val_results = pd.concat((unknownSubstrates_prod, total_val_results_transposed), axis=1)
print(Val_results)

#Write the results onto a CSV file, currently commented out 
#totalResults_df.to_csv("10Runs_ModelResults.csv", index=False)
#Val_results.to_csv("10Runs_ModelResults.csv", index=False, mode="a")

   True Neg  False Pos  False Neg  True Pos       acc  precision 0  \
0     104.0        5.0       12.0      15.0  0.875000     0.896552   
1     103.0        6.0       15.0      12.0  0.845588     0.872881   
2     104.0        5.0       13.0      14.0  0.867647     0.888889   
3     104.0        5.0       14.0      13.0  0.860294     0.881356   
4     104.0        5.0       14.0      13.0  0.860294     0.881356   
5     103.0        6.0       13.0      14.0  0.860294     0.887931   
6     104.0        5.0       15.0      12.0  0.852941     0.873950   
7     104.0        5.0       13.0      14.0  0.867647     0.888889   
8     104.0        5.0       15.0      12.0  0.852941     0.873950   
9     104.0        5.0       14.0      13.0  0.860294     0.881356   

   precision 1  recall 0  recall 1      F1 0      F1 1  
0     0.750000  0.954128  0.555556  0.924444  0.638298  
1     0.666667  0.944954  0.444444  0.907489  0.533333  
2     0.736842  0.954128  0.518519  0.920354  0.608696  
3

In [23]:
#This cell details the alternative settings reports in results section of main text
totalResults_df = pd.DataFrame(columns = ["True Neg","False Pos","False Neg","True Pos", 'acc', 'precision 0',
                                   'precision 1','recall 0', 'recall 1', 'F1 0', 'F1 1'])
val_tot = pd.DataFrame()

matrix_list = []
for x in range(1, 11):
    #Perform training/test set split
    X_train, X_test, y_train, y_test = train_test_split(final, y, test_size=0.15, random_state=31)
    
    #Apply over-sampling to dataset
    sampling_strategy = {1:555, 0:467}
    ros = RandomOverSampler(random_state=10,sampling_strategy =sampling_strategy )
    X_resampled, y_resampled = ros.fit_resample(X_train, y_train)

    # Applies random forest classifier to the dataset
    rfc = RandomForestClassifier(n_estimators=800,max_depth=9)
    rfc.fit(X_resampled,y_resampled)
    
    #Make model predictions
    pred_rfc = rfc.predict(X_test)
    
    #Calculate confusion matrix
    cf_matrix = confusion_matrix(y_test, pred_rfc)
    cf_matrix = np.reshape(cf_matrix,(1,4))
    
    #Calculate sklearn classification metrics
    acc = accuracy_score(y_test, pred_rfc)
    prec = precision_score(y_test, pred_rfc, average=None)
    recall = recall_score(y_test, pred_rfc, average=None)
    F1 = f1_score(y_test, pred_rfc, average=None)
    comb = np.concatenate((cf_matrix, acc, prec, recall, F1), axis=None)
    comb = [comb]
    totalResults_df = totalResults_df.append(pd.DataFrame(comb, columns=totalResults_df.columns), ignore_index=True)
    
    #Evaluate the model on validation set
    ynew = rfc.predict(Xnew)
    validation_prediction_df = pd.DataFrame(ynew, columns = [(x)])
    validation_prediction_df.merge(validation_prediction_df, on=x)
    val_pred_T = validation_prediction_df.T
    val_tot = val_tot.append(val_pred_T)
    
#Print the classification evaluations for model
print(totalResults_df)    
    
unknownSubstrates_prod = unknownSubstrates['Product_Ratio']
total_val_results_transposed = val_tot.T
Val_results = pd.concat((unknownSubstrates_prod, total_val_results_transposed), axis=1)
print(Val_results)

#Write the results onto a CSV file, currently commented out 
#totalResults_df.to_csv("10Runs_ModelResults.csv", index=False)
#Val_results.to_csv("10Runs_ModelResults.csv", index=False, mode="a")

/home/sweav003/envs/CHB/lib/python3.7/site-packages/imblearn/utils/_validation.py:300: UserWarning: After over-sampling, the number of samples (555) in class 1 will be larger than the number of samples in the majority class (class #0 -> 467)
  f"After over-sampling, the number of samples ({n_samples})"
/home/sweav003/envs/CHB/lib/python3.7/site-packages/imblearn/utils/_validation.py:300: UserWarning: After over-sampling, the number of samples (555) in class 1 will be larger than the number of samples in the majority class (class #0 -> 467)
  f"After over-sampling, the number of samples ({n_samples})"
/home/sweav003/envs/CHB/lib/python3.7/site-packages/imblearn/utils/_validation.py:300: UserWarning: After over-sampling, the number of samples (555) in class 1 will be larger than the number of samples in the majority class (class #0 -> 467)
  f"After over-sampling, the number of samples ({n_samples})"
/home/sweav003/envs/CHB/lib/python3.7/site-packages/imblearn/utils/_validation.py:300: U

   True Neg  False Pos  False Neg  True Pos       acc  precision 0  \
0      75.0        5.0        9.0      13.0  0.862745     0.892857   
1      75.0        5.0        8.0      14.0  0.872549     0.903614   
2      75.0        5.0        9.0      13.0  0.862745     0.892857   
3      75.0        5.0        8.0      14.0  0.872549     0.903614   
4      75.0        5.0        8.0      14.0  0.872549     0.903614   
5      75.0        5.0        8.0      14.0  0.872549     0.903614   
6      75.0        5.0        9.0      13.0  0.862745     0.892857   
7      75.0        5.0        8.0      14.0  0.872549     0.903614   
8      75.0        5.0        8.0      14.0  0.872549     0.903614   
9      75.0        5.0        9.0      13.0  0.862745     0.892857   

   precision 1  recall 0  recall 1      F1 0      F1 1  
0     0.722222    0.9375  0.590909  0.914634  0.650000  
1     0.736842    0.9375  0.636364  0.920245  0.682927  
2     0.722222    0.9375  0.590909  0.914634  0.650000  
3

In [25]:
#Let's check unknown compounds for borlation using the reduced matrix
unknownSubstrates=pd.read_csv('NonselectiveValidation.csv')

# Convert validation substrates Inchi's to Mordred and combine into Dataframe with atomic charges and JChem paramters
New_Substrate = unknownSubstrates['Substrate']
New_Substrate_mol_list = []
for inChi_New_Substrate in New_Substrate:
  New_Substrate_mol = Chem.MolFromInchi(inChi_New_Substrate)
  New_Substrate_mol_list.append(New_Substrate_mol)
New_Substrate_img = Draw.MolsToGridImage(New_Substrate_mol_list, molsPerRow=4)
# Puts the new unknown substrate into Pandas Type (Nice columns with Mordred info)
New_Substrate_data = []
New_Substrate_data = calc.pandas(New_Substrate_mol_list)
New_Substrate_data = New_Substrate_data.apply(pd.to_numeric, errors='coerce')
New_Substrate_data.fillna(0, inplace=True)                                                                  
XnewSec = pd.concat((unknownSubstrates, New_Substrate_data), axis=1)
Xnew = XnewSec[selected_feat]

#Display Prediction
ynew = rfc.predict(Xnew)
prediction_df = pd.DataFrame(ynew, columns = ['Prediction'])
unknownSubstrates_prod = unknownSubstrates['Product_Ratio']

results = pd.concat(( unknownSubstrates_prod, prediction_df), axis=1)
results

100%|██████████| 16/16 [00:01<00:00, 14.48it/s]


Product_Ratio  Prediction
0              83           1
1               0           0
2               0           0
3              17           0
4              80           1
5              20           1
6               0           0
7               0           0
8               0           0
9               0           0
10             43           1
11             57           1
12             78           1
13             22           1
14             90           1
15             10           0

In [27]:
#Let's check unknown compounds for borlation using the reduced matrix
unknownSubstrates=pd.read_csv('StaurosporineBoc.csv')

# Convert validation substrates Inchi's to Mordred and combine into Dataframe with atomic charges and JChem paramters
New_Substrate = unknownSubstrates['Substrate']
New_Substrate_mol_list = []
for inChi_New_Substrate in New_Substrate:
  New_Substrate_mol = Chem.MolFromInchi(inChi_New_Substrate)
  New_Substrate_mol_list.append(New_Substrate_mol)
New_Substrate_img = Draw.MolsToGridImage(New_Substrate_mol_list, molsPerRow=4)
# Puts the new unknown substrate into Pandas Type (Nice columns with Mordred info)
New_Substrate_data = []
New_Substrate_data = calc.pandas(New_Substrate_mol_list)
New_Substrate_data = New_Substrate_data.apply(pd.to_numeric, errors='coerce')
New_Substrate_data.fillna(0, inplace=True)                                                                     
XnewSec = pd.concat((unknownSubstrates, New_Substrate_data), axis=1)
Xnew = XnewSec[selected_feat]

#Display Prediction
pd.set_option('display.max_rows', None)
ynew = rfc.predict(Xnew)
prediction_df = pd.DataFrame(ynew, columns = ['Prediction'])
unknownSubstrates_prod = unknownSubstrates['Product_Ratio']

results = pd.concat(( unknownSubstrates_prod, prediction_df), axis=1)
results

100%|██████████| 15/15 [00:10<00:00,  1.43it/s]


Product_Ratio  Prediction
0             NaN           0
1             NaN           0
2             NaN           0
3             NaN           0
4             NaN           0
5             NaN           0
6             NaN           0
7             NaN           0
8             NaN           0
9             NaN           0
10            NaN           0
11            NaN           0
12            NaN           0
13            NaN           0
14            NaN           0